# Predicting the number of cycles in London

In [12]:
import pandas as pd
import numpy as np
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
from plotly import tools
from cycle_flow import *

init_notebook_mode(connected=True)

## Load data

In [13]:
data_df = pd.read_excel('/project/london_cycle_flow/tfl-cycle-flows-tlrn.xlsx', sheet_name=1)

In [14]:
data_df

Comparisons analysis  \
Period and Financial year Start period        End period          Pedal Cycle Counts Indexed Periodic Target Index (adjusted for seasonality) NaN  compared to same period last year   
13_99/00                  NaN                 NaN                 100                        NaN                                              NaN                                NaN   
01_00/01                  NaN                 NaN                 96.27216550241805          NaN                                              NaN                                NaN   
02_00/01                  NaN                 NaN                 102.43148844707147         NaN                                              NaN                                NaN   
03_00/01                  NaN                 NaN                 105.16355454056959         NaN                                              NaN                                NaN   
04_00/01                  NaN                 NaN                 105.13668726491134         NaN                                              NaN                                NaN   
05_00/01                  NaN                 NaN                 102.83617678667383         NaN                                              NaN                                NaN   
06_00/01                  NaN                 NaN                 104.78237506716819         NaN                                              NaN                                NaN   
07_00/01                  NaN                 NaN                 103.95116872649113         NaN                                              NaN                                NaN   
08_00/01                  NaN                 NaN                 102.11411875335841         NaN                                              NaN                                NaN   
09_00/01                  NaN                 NaN                 98.49879097259537          NaN                                              NaN                                NaN   
10_00/01                  NaN                 NaN                 92.572877485223            NaN                                              NaN                                NaN   
11_00/01                  NaN                 NaN                 96.91026329930145          NaN                                              NaN                                NaN   
12_00/01                  NaN                 NaN                 97.01437399247716          NaN                                              NaN                                NaN   
13_00/01                  NaN                 NaN                 96.83134067705535          NaN                                              NaN                                NaN   
01_01/02                  NaN                 NaN                 83.75873186458892          NaN                                              NaN                                NaN   
02_01/02                  NaN                 NaN                 99.77834497581945          NaN                                              NaN                                NaN   
03_01/02                  NaN                 NaN                 102.51712788823214         NaN                                              NaN                                NaN   
04_01/02                  NaN                 NaN                 103.39367275658249         NaN                                              NaN                                NaN   
05_01/02                  NaN                 NaN                 110.43289897904353         NaN                                              NaN                                NaN   
06_01/02                  NaN                 NaN                 105.03761418592154         NaN                                              NaN                                NaN   
07_01/02                  NaN                 NaN                 98.16127082213863          NaN                

## Clean data

In [15]:
cleaner_data = data_df.reset_index().drop(['level_5'], axis=1).dropna()[1:]

In [16]:
renaming = {
    'level_1': 'start',
    'level_2': 'end',
    'level_3': 'cycle_counts',
    'Unnamed: 5': 'avg_temp_c',
    'Unnamed: 7': 'total_rainfall_mm',
    'Unnamed: 8': 'avg_wet_hrs_per_day',
}

to_drop = [
    'level_0',
    'level_4',
    'Comparisons analysis',
    'Unnamed: 1',
    'Unnamed: 2',
    'Unnamed: 3',
    'Unnamed: 4',
    'Unnamed: 6'
]

In [17]:
cleaner_data = cleaner_data.rename(renaming, axis=1).drop(to_drop, axis=1).reset_index()
cleaner_data = cleaner_data.drop('index', axis=1)

In [18]:
cleaner_data

start                  end cycle_counts avg_temp_c  \
0   2010-11-14 00:00:00  2010-12-11 00:00:00      208.174    2.44643   
1   2010-12-12 00:00:00  2011-01-08 00:00:00      125.683      2.375   
2   2011-04-01 00:00:00  2011-04-30 00:00:00      279.636       13.6   
3   2011-05-01 00:00:00  2011-05-28 00:00:00       312.09    14.2071   
4   2011-07-24 00:00:00  2011-08-20 00:00:00      298.191    17.6607   
5   2011-08-21 00:00:00  2011-09-17 00:00:00      271.103    16.0107   
6   2011-09-18 00:00:00  2011-10-15 00:00:00      314.117    15.8107   
7   2011-10-16 00:00:00  2011-11-12 00:00:00      279.749    11.8821   
8   2011-11-13 00:00:00  2011-12-10 00:00:00      264.508    8.30714   
9   2011-12-11 00:00:00  2012-01-07 00:00:00      153.256    7.31071   
10  2012-01-08 00:00:00  2012-02-04 00:00:00      238.471    4.93929   
11  2012-02-05 00:00:00  2012-03-03 00:00:00      233.703       5.85   
12  2012-03-04 00:00:00  2012-03-31 00:00:00      284.221    9.15357   
13  2012-04-01 00:00:00  2012-04-28 00:00:00        253.4    8.34643   
14  2012-04-29 00:00:00  2012-05-26 00:00:00        299.1    12.4179   
15  2012-05-27 00:00:00  2012-06-23 00:00:00        303.5    15.0321   
16  2012-06-24 00:00:00  2012-07-21 00:00:00          306    16.6893   
17  2012-07-22 00:00:00  2012-08-18 00:00:00        374.5    19.1857   
18  2012-08-19 00:00:00  2012-09-15 00:00:00        346.4    17.0286   
19  2012-09-16 00:00:00  2012-10-13 00:00:00        315.7     12.075   
20  2012-10-14 00:00:00  2012-11-10 00:00:00        295.1    9.21429   
21  2012-11-11 00:00:00  2012-12-08 00:00:00        260.5    6.41429   
22  2012-12-09 00:00:00  2013-01-05 00:00:00        176.1    6.98929   
23  2013-01-06 00:00:00  2013-02-02 00:00:00        212.8    3.50714   
24  2013-02-03 00:00:00  2013-03-02 00:00:00        226.3    3.39286   
25  2013-03-03 00:00:00  2013-03-31 00:00:00        223.7    3.50345   
26  2013-04-01 00:00:00  2013-04-27 00:00:00      264.592    8.62593   
27  2013-04-28 00:00:00  2013-05-25 00:00:00      313.801    11.2393   
28  2013-05-26 00:00:00  2013-06-22 00:00:00       316.91    14.4429   
29  2013-06-23 00:00:00  2013-07-20 00:00:00      342.749    19.0071   
30  2013-07-21 00:00:00  2013-08-17 00:00:00      314.807    19.4821   
31  2013-08-18 00:00:00  2013-09-14 00:00:00      293.678    16.8857   
32  2013-09-15 00:00:00  2013-10-12 00:00:00      294.799    13.9393   
33  2013-10-13 00:00:00  2013-11-09 00:00:00      299.399    11.5571   
34  2013-11-10 00:00:00  2013-12-07 00:00:00      315.713       6.25   
35  2013-12-08 00:00:00  2014-01-04 00:00:00      231.297    7.49286   

   total_rainfall_mm avg_wet_hrs_per_day  
0               17.6               1.225  
1               44.8             1.43571  
2                1.8                0.13  
3               22.9            0.346429  
4               43.8            0.739286  
5               65.5             1.23571  
6               11.6            0.571429  
7               33.3             1.18929  
8                9.9            0.510714  
9               74.3             2.41071  
10              24.4            0.939286  
11              12.6            0.714286  
12              21.5            0.935714  
13              83.4             3.23929  
14              61.3               1.825  
15             107.5             3.56071  
16              90.8             2.81786  
17              28.1            0.578571  
18              14.6            0.357143  
19              97.2             2.53571  
20              64.3             2.26429  
21                55             2.36429  
22              92.7             3.18571  
23              51.6             2.75357  
24                30             2.24286  
25              54.1             3.42759  
26              31.7             1.44815  
27              28.8             1.24286  
28              33.3             1.16071  
29               3.9            0.392857  
30              51.5

Define a function that cleans the data.

In [19]:
clean_data_df = clean_data(data_df)

In [20]:
clean_data_df

start                  end cycle_counts avg_temp_c  \
0   2010-11-14 00:00:00  2010-12-11 00:00:00      208.174    2.44643   
1   2010-12-12 00:00:00  2011-01-08 00:00:00      125.683      2.375   
2   2011-04-01 00:00:00  2011-04-30 00:00:00      279.636       13.6   
3   2011-05-01 00:00:00  2011-05-28 00:00:00       312.09    14.2071   
4   2011-07-24 00:00:00  2011-08-20 00:00:00      298.191    17.6607   
5   2011-08-21 00:00:00  2011-09-17 00:00:00      271.103    16.0107   
6   2011-09-18 00:00:00  2011-10-15 00:00:00      314.117    15.8107   
7   2011-10-16 00:00:00  2011-11-12 00:00:00      279.749    11.8821   
8   2011-11-13 00:00:00  2011-12-10 00:00:00      264.508    8.30714   
9   2011-12-11 00:00:00  2012-01-07 00:00:00      153.256    7.31071   
10  2012-01-08 00:00:00  2012-02-04 00:00:00      238.471    4.93929   
11  2012-02-05 00:00:00  2012-03-03 00:00:00      233.703       5.85   
12  2012-03-04 00:00:00  2012-03-31 00:00:00      284.221    9.15357   
13  2012-04-01 00:00:00  2012-04-28 00:00:00        253.4    8.34643   
14  2012-04-29 00:00:00  2012-05-26 00:00:00        299.1    12.4179   
15  2012-05-27 00:00:00  2012-06-23 00:00:00        303.5    15.0321   
16  2012-06-24 00:00:00  2012-07-21 00:00:00          306    16.6893   
17  2012-07-22 00:00:00  2012-08-18 00:00:00        374.5    19.1857   
18  2012-08-19 00:00:00  2012-09-15 00:00:00        346.4    17.0286   
19  2012-09-16 00:00:00  2012-10-13 00:00:00        315.7     12.075   
20  2012-10-14 00:00:00  2012-11-10 00:00:00        295.1    9.21429   
21  2012-11-11 00:00:00  2012-12-08 00:00:00        260.5    6.41429   
22  2012-12-09 00:00:00  2013-01-05 00:00:00        176.1    6.98929   
23  2013-01-06 00:00:00  2013-02-02 00:00:00        212.8    3.50714   
24  2013-02-03 00:00:00  2013-03-02 00:00:00        226.3    3.39286   
25  2013-03-03 00:00:00  2013-03-31 00:00:00        223.7    3.50345   
26  2013-04-01 00:00:00  2013-04-27 00:00:00      264.592    8.62593   
27  2013-04-28 00:00:00  2013-05-25 00:00:00      313.801    11.2393   
28  2013-05-26 00:00:00  2013-06-22 00:00:00       316.91    14.4429   
29  2013-06-23 00:00:00  2013-07-20 00:00:00      342.749    19.0071   
30  2013-07-21 00:00:00  2013-08-17 00:00:00      314.807    19.4821   
31  2013-08-18 00:00:00  2013-09-14 00:00:00      293.678    16.8857   
32  2013-09-15 00:00:00  2013-10-12 00:00:00      294.799    13.9393   
33  2013-10-13 00:00:00  2013-11-09 00:00:00      299.399    11.5571   
34  2013-11-10 00:00:00  2013-12-07 00:00:00      315.713       6.25   
35  2013-12-08 00:00:00  2014-01-04 00:00:00      231.297    7.49286   

   total_rainfall_mm avg_wet_hrs_per_day  
0               17.6               1.225  
1               44.8             1.43571  
2                1.8                0.13  
3               22.9            0.346429  
4               43.8            0.739286  
5               65.5             1.23571  
6               11.6            0.571429  
7               33.3             1.18929  
8                9.9            0.510714  
9               74.3             2.41071  
10              24.4            0.939286  
11              12.6            0.714286  
12              21.5            0.935714  
13              83.4             3.23929  
14              61.3               1.825  
15             107.5             3.56071  
16              90.8             2.81786  
17              28.1            0.578571  
18              14.6            0.357143  
19              97.2             2.53571  
20              64.3             2.26429  
21                55             2.36429  
22              92.7             3.18571  
23              51.6             2.75357  
24                30             2.24286  
25              54.1             3.42759  
26              31.7             1.44815  
27              28.8             1.24286  
28              33.3             1.16071  
29               3.9            0.392857  
30              51.5

In [21]:
clean_data_df.equals(cleaner_data)

True

## Plot

In [22]:
plot_seasonality(clean_data_df)

In [23]:
plot2d(clean_data_df)

This is the format of your plot grid:
[ (1,1) x1,y1 ]  [ (1,2) x2,y2 ]



In [51]:
trace = go.Scatter(
    x = clean_data_df['avg_temp_c'],
    y = clean_data_df['cycle_counts'],
    mode = 'markers'
)

data = [trace]

layout = go.Layout(
    height=600,
    width=600,
    xaxis = dict(
        title='average temperature (C)'
    ),
    yaxis = dict(
        title='cycle counts'
    )
)

fig = go.Figure(data=data, layout=layout)

iplot(fig)

Plot the clycle flow against the total rainfall and the average temperature.

In [24]:
plot3d(clean_data_df)

## Train a linear regressor on the data and export the model

In [57]:
from sklearn.linear_model import LinearRegression

In [58]:
X = clean_data_df[['total_rainfall_mm', 'avg_temp_c']]

Y = np.array(clean_data_df['cycle_counts'])
Y = Y.reshape((len(Y),1))

In [59]:
lr = LinearRegression()

In [60]:
lr.fit(X, Y)

LinearRegression(copy_X=True, fit_intercept=True, n_jobs=1, normalize=False)

In [61]:
from sklearn.externals import joblib

In [62]:
joblib.dump(lr, 'model.pkl')

['model.pkl']

## Create grid to plot the predictions from the trained model

In [32]:
xc = np.linspace(0, 120, 100)
yc = np.linspace(0, 20, 100)

In [33]:
xgrid, ygrid = np.meshgrid(xc, yc)

In [34]:
grid = np.vstack((xgrid.flatten(),ygrid.flatten())).T

In [35]:
lr.predict(grid)

array([[198.615916  ],
       [198.26446037],
       [197.91300474],
       ...,
       [327.34574624],
       [326.99429061],
       [326.64283498]])

In [36]:
cleaner_data['total_rainfall_mm'].shape

(36,)

In [37]:
trace1 = go.Scatter3d(
    x = cleaner_data['total_rainfall_mm'],
    y = cleaner_data['avg_temp_c'],
    z = cleaner_data['cycle_counts'],
    mode = 'markers',
    marker=dict(
        size=5
    ),
    name = 'data'
)

trace2 = go.Scatter3d(
    x = grid[:,0],
    y = grid[:,1],
    z = lr.predict(grid).flatten(),
    mode = 'markers',
    marker=dict(
        size=1,
        color='rgb(255,255,102)',
        opacity=0.6
    ),
    name = 'prediction'
)

data = [trace1, trace2]

new_rainfall = 80.0
new_temperature = 10.0
new_rainfall = np.array([new_rainfall])
new_temperature = np.array([new_temperature])

trace3 = go.Scatter3d(
    x = new_rainfall,
    y = new_temperature,
    z = lr.predict(np.vstack((new_rainfall, new_temperature)).T).flatten(),
    name = 'new prediction',
    mode = 'markers',
    marker=dict(
        size=5,
        color='red'
    )
)

data.append(trace3)

layout = go.Layout(
    margin = dict(
        t = 50,
        b = 50
    ),
    scene = dict(
        xaxis = dict(
            title = 'total rainfall (mm)'
        ),
        yaxis = dict(
            title = 'average temperature (C)'
        ),
        zaxis = dict(
            title = 'cycle counts'
        )
    )
)

fig = go.Figure(data=data, layout=layout)

iplot(fig)

In [38]:
plot_predictions(clean_data_df, grid, lr)

In [39]:
grid2 = create_grid()

In [40]:
plot_predictions(clean_data_df, grid2, lr)

In [41]:
from sklearn.metrics import r2_score

In [42]:
training_error = r2_score(Y, lr.predict(X))

In [43]:
print(f'Training error (r2 score): {training_error}')

Training error (r2 score): 0.6514488442532727


Save the trained model.

In [44]:
from sklearn.externals import joblib

In [45]:
joblib.dump(lr, 'model.pkl')

['model.pkl']

Reload the saved model.

In [46]:
lr2 = joblib.load('/project/london_cycle_flow/london-cycle-flow/model.pkl')

In [47]:
grid2 = create_grid()

In [48]:
plot_predictions(clean_data_df, grid2, lr2)